In [1]:
# imports
import requests
import os
import json
import pandas as pd

# Foursquare

Send a request to Foursquare with a small radius (1000m) for all the bike stations in your city of choice. 

In [9]:
key = os.environ["FOURSQUARE_KEY"]
headers = {
    "accept": "application/json",
    "Authorization": key
}

foursquare_poi = {}

for station in stations[:250]: # Using 250 stations for processing time
    url = "https://api.foursquare.com/v3/places/search?ll=" + str(station["latitude"]) + "%2C" + str(station["longitude"]) + "&radius=1000&fields=name,categories,location,distance,rating&sort=RELEVANCE"
    response = json.loads(requests.get(url, headers=headers).text)
    foursquare_poi[station["station_name"]] = response

print(foursquare_poi)

{'001023 - River Street , Clerkenwell': {'results': [{'categories': [{'id': 17068, 'name': 'Gourmet Store', 'short_name': 'Gourmet', 'plural_name': 'Gourmet Stores', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/food_gourmet_', 'suffix': '.png'}}], 'distance': 23, 'location': {'address': '25a Lloyd Baker St', 'admin_region': 'England', 'country': 'GB', 'cross_street': '', 'formatted_address': '25a Lloyd Baker St, London, Greater London, WC1X 9AT', 'locality': 'London', 'post_town': 'London', 'postcode': 'WC1X 9AT', 'region': 'Greater London'}, 'name': 'Myddeltons Delicatessen', 'rating': 7.3}, {'categories': [{'id': 16032, 'name': 'Park', 'short_name': 'Park', 'plural_name': 'Parks', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/parks_outdoors/park_', 'suffix': '.png'}}], 'distance': 150, 'location': {'address': '42 Myddelton Square', 'admin_region': 'England', 'country': 'GB', 'cross_street': '', 'formatted_address': '42 Myddelton Square, London, Greate

Parse through the response to get the POI (such as restaurants, bars, etc) details you want (ratings, name, location, etc)

In [10]:
clean_foursquare_poi = []

for station in foursquare_poi:
    for poi in foursquare_poi[station]["results"]:
        clean_foursquare_poi.append(
            {
                "station_name": station,
                "station_distance_(m)": poi["distance"],
                "loc_address": poi["location"]["formatted_address"],
                "loc_name": poi["name"],
                "loc_category": poi["categories"][0]["name"] if poi["categories"] else None,
                "loc_rating": poi.get("rating", None)
            }
        )

Put your parsed results into a DataFrame

In [11]:
foursquare_df = pd.DataFrame(clean_foursquare_poi)
foursquare_df

station_name  station_distance_(m)  \
0          001023 - River Street , Clerkenwell                    23   
1          001023 - River Street , Clerkenwell                   150   
2          001023 - River Street , Clerkenwell                   280   
3          001023 - River Street , Clerkenwell                   294   
4          001023 - River Street , Clerkenwell                   325   
...                                        ...                   ...   
2495  200191 - Spencer Park, Wandsworth Common                   346   
2496  200191 - Spencer Park, Wandsworth Common                   374   
2497  200191 - Spencer Park, Wandsworth Common                   603   
2498  200191 - Spencer Park, Wandsworth Common                   602   
2499  200191 - Spencer Park, Wandsworth Common                   597   

                                            loc_address  \
0     25a Lloyd Baker St, London, Greater London, WC...   
1     42 Myddelton Square, London, Greater London, E...   
2     23 Arlington Way, London, Greater London, EC1R...   
3     96-98 Pentonville Rd, London, Greater London, ...   
4      399 St John St, London, Greater London, EC1V 4LD   
...                                                 ...   
2495  123 St John's Hill (Vardens Rd), Wandsworth, G...   
2496  162 St John's Hill, London, Greater London, SW...   
2497  69 Northcote Rd, London, Greater London, SW11 1NP   
2498  76 Northcote Rd, Battersea, Greater London, SW...   
2499  74 Northcote Rd, London, Greater London, SW11 6QL   

                     loc_name    loc_category  loc_rating  
0     Myddeltons Delicatessen   Gourmet Store         7.3  
1            Myddelton Square            Park         8.2  
2           Present & Correct          Retail         8.8  
3               The Lexington       Rock Club         8.4  
4             Turner & George         Butcher         8.8  
...                       ...             ...         ...  
2495                Birdhouse     Coffee Shop         8.2  
2496  St Johns Therapy Centre  Medical Center         6.7  
2497          Oddono's Gelati          Bakery         8.7  
2498             Franco Manca        Pizzeria         8.4  
2499          MEATliquor SW11    Burger Joint         7.9  

[2500 rows x 6 columns]

# Yelp

Send a request to Yelp with a small radius (1000m) for all the bike stations in your city of choice. 

In [12]:
key = os.environ["YELP_KEY"]
headers = {
    "accept": "application/json",
    "Authorization": f"Bearer {key}"
}

yelp_poi = {}

for station in stations[:250]:
    url = "https://api.yelp.com/v3/businesses/search?latitude=" + str(station["latitude"]) + "&longitude=" + str(station["longitude"]) + "&radius=1000&categories=&sort_by=best_match&limit=10" # Match Foursquare default limit of 10
    response = json.loads(requests.get(url, headers=headers).text)
    yelp_poi[station["station_name"]] = response

print(yelp_poi)

{'001023 - River Street , Clerkenwell': {'businesses': [{'id': 'ruccgDIBllsprKlP_7HBpg', 'alias': 'the-easton-london', 'name': 'The Easton', 'image_url': 'https://s3-media2.fl.yelpcdn.com/bphoto/LA2l8-UXYQ5zr6i9FUmwRA/o.jpg', 'is_closed': False, 'url': 'https://www.yelp.com/biz/the-easton-london?adjust_creative=jKk1rj_KrblfNrLJ_qI6oA&utm_campaign=yelp_api_v3&utm_medium=api_v3_business_search&utm_source=jKk1rj_KrblfNrLJ_qI6oA', 'review_count': 37, 'categories': [{'alias': 'pubs', 'title': 'Pubs'}, {'alias': 'gastropubs', 'title': 'Gastropubs'}], 'rating': 4.5, 'coordinates': {'latitude': 51.526323227476, 'longitude': -0.11139933433552}, 'transactions': [], 'price': '££', 'location': {'address1': '22 Easton Street', 'address2': '', 'address3': '', 'city': 'London', 'zip_code': 'WC1X 0DS', 'country': 'GB', 'state': 'XGL', 'display_address': ['22 Easton Street', 'London WC1X 0DS', 'United Kingdom']}, 'phone': '+442072787608', 'display_phone': '+44 20 7278 7608', 'distance': 330.92630873133

Parse through the response to get the POI (such as restaurants, bars, etc) details you want (ratings, name, location, etc)

In [13]:
clean_yelp_poi = []

for station in yelp_poi:
    for poi in yelp_poi[station]["businesses"]:
        clean_yelp_poi.append(
            {
                "station_name": station,
                "station_distance_(m)": round(poi["distance"]),
                "loc_address": poi["location"]["address1"],
                "loc_name": poi["name"],
                "loc_category": poi["categories"][0]["title"] if poi["categories"] else None,
                "loc_rating": poi["rating"]
            }
        )

Put your parsed results into a DataFrame

In [14]:
yelp_df = pd.DataFrame(clean_yelp_poi)
yelp_df

station_name  station_distance_(m)  \
0          001023 - River Street , Clerkenwell                   331   
1          001023 - River Street , Clerkenwell                   362   
2          001023 - River Street , Clerkenwell                   342   
3          001023 - River Street , Clerkenwell                   946   
4          001023 - River Street , Clerkenwell                   336   
...                                        ...                   ...   
2495  200191 - Spencer Park, Wandsworth Common                   680   
2496  200191 - Spencer Park, Wandsworth Common                  1056   
2497  200191 - Spencer Park, Wandsworth Common                   598   
2498  200191 - Spencer Park, Wandsworth Common                   884   
2499  200191 - Spencer Park, Wandsworth Common                   708   

                loc_address             loc_name        loc_category  \
0          22 Easton Street           The Easton                Pubs   
1     52 Lloyd Baker Street         Union Tavern                Pubs   
2        69 Rosebery Avenue       The Wilmington                Pubs   
3         80 Liverpool Road  The Pig and Butcher             British   
4      59-61 Exmouth Market              Santore             Italian   
...                     ...                  ...                 ...   
2495      64 Battersea Rise    Pizza Metro Pizza               Pizza   
2496        105 Falcon Road        Fish in a Tie       Mediterranean   
2497      87 Battersea Rise           Dip & Flip             Burgers   
2498     5-9 Battersea Rise   The Breakfast Club  Breakfast & Brunch   
2499   50-52 Battersea Rise                  Pho          Vietnamese   

      loc_rating  
0            4.5  
1            4.5  
2            4.5  
3            4.5  
4            4.5  
...          ...  
2495         4.0  
2496         4.0  
2497         4.0  
2498         4.0  
2499         4.0  

[2500 rows x 6 columns]

# Comparing Results

Which API provided you with more complete data? Provide an explanation. 

'''

Both APIs actually provided enough data for the information relevant to what I am comparing. By using the API parameters and field filtering, I can find the name, location, rating, etc. for all POIs. However, the rating scale provided by the APIs is different; Foursquare provides ratings on a scale /10, whereas Yelp uses a rating scale /5. This will make it difficult to compare the ratings of POIs that are sourced from different APIs.

'''

Get the top 10 restaurants according to their rating

In [15]:
foursquare_restaurants = foursquare_df.loc[foursquare_df["loc_category"] == "Restaurant"]
foursquare_restaurants = foursquare_restaurants.sort_values(by="loc_rating", ascending=False)
foursquare_restaurants.head(10)

station_name  station_distance_(m)  \
318               001042 - Woodstock Street, Mayfair                   196   
1003            001152 - Marylebone Lane, Marylebone                   149   
1930          200165 - Wellington Row, Bethnal Green                    86   
484              001123 - Southampton Place, Holborn                   243   
1272               002649 - Sardinia Street, Holborn                   248   
227               000975 - Theobald's Road , Holborn                   358   
1394                  200035 - Walmer Road, Avondale                   636   
1002            001152 - Marylebone Lane, Marylebone                   142   
130      003445 - Shoreditch High Street, Shoreditch                   120   
1136  002636 - Prince Albert Road, The Regent's Park                   559   

                                            loc_address  \
318   6 Medici Courtyard, London, Greater London, W1...   
1003  23 Barrett St (at Barrett St), Marylebone, Gre...   
1930  49 Columbia Rd, Shoreditch, Greater London, E2...   
484   252 High Holborn, London, Greater London, WC1V...   
1272  252 High Holborn, London, Greater London, WC1V...   
227   252 High Holborn, London, Greater London, WC1V...   
1394  92 Kensington Park Rd, Notting Hill, Greater L...   
1002  75 Davies St (West One Shopping Centre), Londo...   
130        380 Old St, London, Greater London, EC1V 9LT   
1136  38 St John's Wood Terrace, London, Greater Lon...   

                    loc_name loc_category  loc_rating  
318        The MAINE Mayfair   Restaurant         9.3  
1003  St Christopher's Place   Restaurant         9.2  
1930                   Brawn   Restaurant         9.2  
484              Mirror Room   Restaurant         9.0  
1272             Mirror Room   Restaurant         9.0  
227              Mirror Room   Restaurant         9.0  
1394     Core by Clare Smyth   Restaurant         9.0  
1002         Joe & the Juice   Restaurant         8.9  
130           The Clove Club   Restaurant         8.9  
1136    Drunch Regent's Park   Restaurant         8.9

In [16]:
restaurants = ["Restaurant", "Chinese", "Lebanese", "Vietnamese", "Italian", "British", "Pizza", "Turkish", "Sandwiches"] # The Yelp API doesn't categorize restaurants as a general term

yelp_restaurants = yelp_df.loc[yelp_df["loc_category"].isin(restaurants)]
yelp_restaurants = yelp_restaurants.sort_values(by="loc_rating", ascending=False)
yelp_restaurants.head(10)

station_name  station_distance_(m)  \
477        003478 - Guildhouse Street, Victoria                   190   
558            003460 - Warwick Square, Pimlico                   238   
88            000993 - Drummond Street , Euston                    61   
1909             200010 - Manresa Road, Chelsea                   861   
332   001055 - Wellington Road, St. John's Wood                   660   
1875              200153 - Blythe Road, Olympia                   283   
294              001045 - Jewry Street, Aldgate                   166   
1920       200167 - Twig Folly Bridge, Mile End                    21   
1198             001218 - Flood Street, Chelsea                   564   
1857              200160 - Langdon Park, Poplar                   283   

                 loc_address                     loc_name loc_category  \
477        46 Churton Street                 Cacio & Pepe      Italian   
558        46 Churton Street                 Cacio & Pepe      Italian   
88       131 Drummond Street                     Brizzi's      Italian   
1909  8-9 Blacklands Terrace              The Five Fields      British   
332       1 Blenheim Terrace           Yasmeen Restaurant     Lebanese   
1875          71 Blythe Road                    Pentolina      Italian   
294   49 Aldgate High Street                      Satyrio      Italian   
1920          238 Roman Road           Palmers Restaurant      British   
1198  8-9 Blacklands Terrace              The Five Fields      British   
1857            6 Market Way  Maureen's Pie And Mash Shop      British   

      loc_rating  
477          5.0  
558          5.0  
88           5.0  
1909         5.0  
332          5.0  
1875         5.0  
294          5.0  
1920         5.0  
1198         5.0  
1857         5.0